In [1]:
!pipwin install pyaudio

Package `pyaudio` found in cache
https://download.lfd.uci.edu/pythonlibs/w6tyco5e/PyAudio-0.2.11-cp38-cp38-win_amd64.whl
PyAudio-0.2.11-cp38-cp38-win_amd64.whl
[*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]    [*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]    [*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]    [*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]    [*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]    [*] 0 bytes / 110 kB @ 0 bytes/s [------------------] [0.0%, 0s left]   

In [2]:
!pip install sounddevice

In [3]:
!pip install SpeechRecognition

In [1]:
import pyaudio
from six.moves import queue
import time
import sounddevice as sd
from scipy.io.wavfile import write
import os
import glob
import IPython.display
import cosine_similarity as cs
import freq_dataset as fd
cos = cs.CosineSimilarity()
freq = fd.MakeFreqDataset()

In [2]:
# 녹음용 값 16kHz
RATE = 16000
#버퍼는 1600
CHUNK = int(RATE / 10)

In [3]:
pa = pyaudio.PyAudio()
pa.get_default_output_device_info()

{'index': 4,
 'structVersion': 2,
 'name': '헤드폰(JBL TUNE660NC Stereo)',
 'hostApi': 0,
 'maxInputChannels': 0,
 'maxOutputChannels': 2,
 'defaultLowInputLatency': 0.09,
 'defaultLowOutputLatency': 0.09,
 'defaultHighInputLatency': 0.18,
 'defaultHighOutputLatency': 0.18,
 'defaultSampleRate': 44100.0}

In [4]:
pa.get_device_count()

39

In [5]:
pa.get_default_input_device_info()

{'index': 1,
 'structVersion': 2,
 'name': '머리에 거는 수화기(JBL TUNE660NC Hands-',
 'hostApi': 0,
 'maxInputChannels': 1,
 'maxOutputChannels': 0,
 'defaultLowInputLatency': 0.09,
 'defaultLowOutputLatency': 0.09,
 'defaultHighInputLatency': 0.18,
 'defaultHighOutputLatency': 0.18,
 'defaultSampleRate': 44100.0}

In [6]:
import speech_recognition as sr
r = sr.Recognizer()
with sr.Microphone(device_index=1) as source:
    r.adjust_for_ambient_noise(source)
    audio = r.listen(source)

In [14]:
print(pa.get_default_output_device_info())

{'index': 4, 'structVersion': 2, 'name': '헤드폰(JBL TUNE660NC Stereo)', 'hostApi': 0, 'maxInputChannels': 0, 'maxOutputChannels': 2, 'defaultLowInputLatency': 0.09, 'defaultLowOutputLatency': 0.09, 'defaultHighInputLatency': 0.18, 'defaultHighOutputLatency': 0.18, 'defaultSampleRate': 44100.0}


In [15]:
import sounddevice as sd
print(sd.query_devices())

   0 Microsoft Sound Mapper - Input, MME (2 in, 0 out)
>  1 머리에 거는 수화기(JBL TUNE660NC Hands-, MME (2 in, 0 out)
   2 Microphone Array(인텔® 스마트 사운드 기술, MME (2 in, 0 out)
   3 Microsoft Sound Mapper - Output, MME (0 in, 2 out)
<  4 헤드폰(JBL TUNE660NC Stereo), MME (0 in, 2 out)
   5 머리에 거는 수화기(JBL TUNE660NC Hands-, MME (0 in, 2 out)
   6 Speakers(Realtek(R) Audio), MME (0 in, 2 out)
   7 주 사운드 캡처 드라이버, Windows DirectSound (2 in, 0 out)
   8 머리에 거는 수화기(JBL TUNE660NC Hands-Free AG Audio), Windows DirectSound (2 in, 0 out)
   9 Microphone Array(인텔® 스마트 사운드 기술), Windows DirectSound (2 in, 0 out)
  10 주 사운드 드라이버, Windows DirectSound (0 in, 2 out)
  11 헤드폰(JBL TUNE660NC Stereo), Windows DirectSound (0 in, 2 out)
  12 머리에 거는 수화기(JBL TUNE660NC Hands-Free AG Audio), Windows DirectSound (0 in, 1 out)
  13 Speakers(Realtek(R) Audio), Windows DirectSound (0 in, 2 out)
  14 머리에 거는 수화기(JBL TUNE660NC Hands-Free AG Audio), Windows WASAPI (0 in, 1 out)
  15 Speakers(Realtek(R) Audio), Windows WASAPI (0 in, 2

In [7]:
p = pyaudio.PyAudio()
info = p.get_host_api_info_by_index(0)
numdevices = info.get('deviceCount')
for i in range(0, numdevices):
    if (p.get_device_info_by_host_api_device_index(0, i).get('maxInputChannels')) > 0:
        print("Input Device id ", i, " - ", p.get_device_info_by_host_api_device_index(0, i).get('name'))

Input Device id  0  -  Microsoft Sound Mapper - Input
Input Device id  1  -  머리에 거는 수화기(JBL TUNE660NC Hands-
Input Device id  2  -  Microphone Array(인텔® 스마트 사운드 기술


In [8]:
info.get('deviceCount')

7

In [20]:
import pyaudio
import wave
 
FORMAT = pyaudio.paInt16
CHANNELS = 1
RATE = 44100
CHUNK = 512
RECORD_SECONDS = 5
WAVE_OUTPUT_FILENAME = "recordedFile.wav"
device_index = 2
audio = pyaudio.PyAudio()

print("----------------------record device list---------------------")
info = audio.get_host_api_info_by_index(0)
numdevices = info.get('deviceCount')
for i in range(0, numdevices):
        if (audio.get_device_info_by_host_api_device_index(0, i).get('maxInputChannels')) > 0:
            print("Input Device id ", i, " - ", audio.get_device_info_by_host_api_device_index(0, i).get('name'))

print("-------------------------------------------------------------")

index = int(input())
print("recording via index "+str(index))

stream = audio.open(format=FORMAT, channels=CHANNELS,
                rate=RATE, input=True,input_device_index = index,
                frames_per_buffer=CHUNK)
print ("recording started")
Recordframes = []
 
for i in range(0, int(RATE / CHUNK * RECORD_SECONDS)):
    data = stream.read(CHUNK)
    Recordframes.append(data)
print ("recording stopped")
 
stream.stop_stream()
stream.close()
audio.terminate()
 
waveFile = wave.open(WAVE_OUTPUT_FILENAME, 'wb')
waveFile.setnchannels(CHANNELS)
waveFile.setsampwidth(audio.get_sample_size(FORMAT))
waveFile.setframerate(RATE)
waveFile.writeframes(b''.join(Recordframes))
waveFile.close()

----------------------record device list---------------------
Input Device id  0  -  Microsoft Sound Mapper - Input
Input Device id  1  -  머리에 거는 수화기(JBL TUNE660NC Hands-
Input Device id  2  -  Microphone Array(인텔® 스마트 사운드 기술
-------------------------------------------------------------
1
recording via index 1
recording started
recording stopped


In [9]:
def play_song(path):
    (file_dir, file_id) = os.path.split(path)
    print(file_id[:-4])
    return IPython.display.display(IPython.display.Audio(path))
def play_song_ls(cm_lr_df):
    for idx, path in enumerate(cm_lr_df['path']):
        print(cm_lr_df['pred'].iloc[idx])
        play_song(path)

In [48]:
def record_freq(label, path="sounds/", fs=44100, seconds=5):
    """fs = 44100  # Sample rate
       seconds = 5  # Duration of recording"""
    print("start recording...")
    myrecording = sd.rec(int(seconds * fs), samplerate=fs, channels=2)
    sd.wait()  # Wait until recording is finished
    filename = f"{label}_{time.strftime('%Y%m%d_%H%M%S')}"
    write(path+filename+".wav", fs, myrecording)  # Save as WAV file 
    print("file save success")
    play_song(path+filename+".wav")
    
    o_path = list(set(glob.glob(f'{path}*')))
    path_ls = [file for file in o_path if file.endswith(".mp3") or file.endswith(".wav")]
    name_ls = [name.split("\\")[-1][:-4] for name in path_ls]
    # label_ls = [name.split('/')[-3] for name in path_ls]
    info_df = pd.DataFrame()
    info_df['path'] = path_ls
    # info_df['label'] = label_ls
    info_df['name'] = name_ls
    
    freq_df = freq.make_frequency_df(tracks_df=info_df[info_df['name']==filename])
    return freq_df

In [25]:
play_song('output.wav')

output


In [49]:
freq_df = record_sound("noise")
freq_df

start recording...
file save success
noise_20211203_184746


100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:01<00:00,  1.26s/it]


name                              path  duration  \
0  noise_20211203_184746  sounds\noise_20211203_184746.wav       5.0   

   chroma_stft_mean  chroma_stft_var  rms_mean   rms_var  \
0          0.263047         0.096326  0.001054  0.000006   

   spectral_centroid_mean  spectral_centroid_var  spectral_bandwidth_mean  \
0             2228.494482          699687.245173              2084.788164   

   ...  mfcc16_mean  mfcc16_var  mfcc17_mean  mfcc17_var  mfcc18_mean  \
0  ...    -2.786011   83.746475     -3.94172   88.134308    -7.968068   

   mfcc18_var  mfcc19_mean  mfcc19_var  mfcc20_mean  mfcc20_var  
0   59.268562    -5.890416   93.717476    -7.202215   42.285618  

[1 rows x 60 columns]